In [108]:
# Работа с табличными данными
import pandas as pd
import numpy as np

# Пайплайн
from sklearn.pipeline import Pipeline
from sklearn.base import BaseEstimator, TransformerMixin

# Преобразование признаков
from sklearn.preprocessing import MinMaxScaler, RobustScaler, StandardScaler

# Модели
from sklearn.linear_model import LogisticRegression

# Валидация
from sklearn.model_selection import cross_val_predict, cross_val_score
from sklearn.metrics import f1_score, accuracy_score, classification_report
from sklearn.model_selection import train_test_split

# Визуализация
import plotly.express as px
import plotly.io as pio
pio.templates.default = 'plotly_dark'

from collections import deque

from motorica.utils import *

from typing import Any

## Базовое решение с использованием *Logistic Regression*

In [109]:
METAINFO_PATH = 'marked/selected_montages.csv'
read_meta_info(METAINFO_PATH)

pilote_id  last_train_idx  \
montage                                                              
2023-05-15_16-16-08.palm                         1           23337   
2023-05-15_17-12-24.palm                         1           23336   
2023-06-05_16-12-38.palm                         1           17939   
2023-06-05_17-53-01.palm                         1           17771   
2023-06-20_14-43-11.palm                         1           17936   
2023-06-20_13-30-15.palm                         1           17928   
2023-06-20_12-34-17.palm                         1           17758   
2023-09-30_08-06-44.palm                         2            5693   
2023-09-29_11-03-50.palm                         2            5694   
2023-09-29_09-20-47.palm                         2            5690   
2023-09-13_22-14-05.palm                         2            2769   
2023-09-12_14-59-23.palm                         2            2759   
2023-09-12_12-55-22.palm                         2            2760   
2023-05-31_17-14-41.palm                         2           15679   
2023-05-31_15-46-37.palm                         2           15676   
2023-05-22_20-22-01.palm                         2           15602   
2023-05-22_17-04-29.palm                         2           23289   
2023-05-19_12-04-02.palm                         2           23297   
2023-04-18_19-08-47 gestures train.palm          3           29532   
2023-05-07_16-54-27.palm                         3            5747   
2023-05-07_15-19-05.palm                         3            5361   
2023-05-05_17-57-30.palm                         4           20756   

                                         len(train)  len(test)  ts_delta  \
montage                                                                    
2023-05-15_16-16-08.palm                      23337       5810      33.0   
2023-05-15_17-12-24.palm                      23336       5803      33.0   
2023-06-05_16-12-38.palm                      17939       4431      33.0   
2023-06-05_17-53-01.palm                      17771       4435      33.0   
2023-06-20_14-43-11.palm                      17936       4441      33.0   
2023-06-20_13-30-15.palm                      17928       4435      33.0   
2023-06-20_12-34-17.palm                      17758       4444      33.0   
2023-09-30_08-06-44.palm                       5693       5509      33.0   
2023-09-29_11-03-50.palm                       5694       5511      33.0   
2023-09-29_09-20-47.palm                       5690       5507      33.0   
2023-09-13_22-14-05.palm                       2769       2951      33.0   
2023-09-12_14-59-23.palm                       2759       2944      33.0   
2023-09-12_12-55-22.palm                       2760       2944      33.0   
2023-05-31_17-14-41.palm                      15679       3891      33.0   
2023-05-31_15-46-37.palm                      15676       3892      33.0   
2023-05-22_20-22-01.palm                      15602       3872      33.0   
2023-05-22_17-04-29.palm                      23289       5796      33.0   
2023-05-19_12-04-02.palm                      23297       5795      33.0   
2023-04-18_19-08-47 gestures train.palm       29532       8078      33.0   
2023-05-07_16-54-27.palm                       5747       5569      33.0   
2023-05-07_15-19-05.palm                       5361       5884      33.0   
2023-05-05_17-57-30.palm                      20756       5894      33.0   

                                         ticks_per_gest  n_gestures   ACC  \
montage                                                                     
2023-05-15_16-16-08.palm                           46.0       271.0  True   
2023-05-15_17-12-24.palm                           46.0       271.0  True   
2023-06-05_16-12-38.palm                           30.0       361.0  True   
2023-06-05_17-53-01.palm                           31.0       361.0  True   
2023-06-20_14-43-11.palm                           31.0       361.0  True

In [110]:
def read_train_and_test(
        montage: str,
        features: List[str], 
        target_col: str = 'act_label',
        subdir: str = 'marked/'
) -> List:
    
    data_train = pd.read_csv(subdir + montage + ".train", index_col=0)
    data_test = pd.read_csv(subdir + montage + ".test", index_col=0)
    data_full = pd.read_csv(subdir + montage + ".marked", index_col=None)
    X_train = data_train.drop(target_col, axis=1)[features]
    y_train = data_train[target_col]
    X_test = data_test.drop(target_col, axis=1)[features]
    y_test = data_test[target_col]
    return X_train, X_test, y_train, y_test, data_full

In [111]:
montage = "2023-05-22_17-04-29.palm"
montage = "2023-05-22_20-22-01.palm"
montage_info = read_meta_info(METAINFO_PATH).loc[montage]

print(montage)
display(montage_info)

features = montage_info['hi_val_sensors'] + cols_gyr

X_train, X_test, y_train, y_test, _ = read_train_and_test(montage, features)

scaler = MinMaxScaler()
X_train_scaled = pd.DataFrame(
    scaler.fit_transform(X_train),
    columns=X_train.columns
)
X_test_scaled = pd.DataFrame(
    scaler.transform(X_test),
    columns=X_test.columns
)

2023-05-22_20-22-01.palm


pilote_id                                                         2
last_train_idx                                                15602
len(train)                                                    15602
len(test)                                                      3872
ts_delta                                                       33.0
ticks_per_gest                                                 46.0
n_gestures                                                    181.0
ACC                                                            True
GYR                                                            True
hi_val_sensors    [5, 7, 9, 10, 15, 18, 20, 23, 26, 28, 34, 37, 39]
mark_sensors             [7, 9, 10, 18, 20, 23, 26, 28, 34, 37, 39]
Name: 2023-05-22_20-22-01.palm, dtype: object

In [112]:
lr = LogisticRegression(C=500, max_iter=5000)
lr.fit(X_train_scaled, y_train)

y_pred = lr.predict(X_test_scaled)

#proba = lr.predict_proba(X_test_scaled)
#y_proba = np.array([p[y_pred[i]] for i, p in enumerate(proba)])

In [113]:
fig_data = X_test.copy()
fig_data['true'] = y_test * 100
fig_data['pred'] = y_pred * 100
#fig_data['proba'] = y_proba * 100

fig = px.line(fig_data, width=1000, height=700, title=montage)
fig.update_traces(line=dict(width=1))

In [114]:
print(classification_report(y_test, y_pred, zero_division=0))

              precision    recall  f1-score   support

           0       0.96      0.97      0.97      2666
           1       0.95      0.94      0.95       249
           2       0.95      0.96      0.96       257
           3       1.00      0.88      0.93       234
           4       0.85      0.99      0.92       201
           5       0.93      0.84      0.89       262

    accuracy                           0.96      3869
   macro avg       0.94      0.93      0.94      3869
weighted avg       0.96      0.96      0.96      3869



## Использование лаговых признаков

In [115]:
class LagWrapper(BaseEstimator, TransformerMixin):

    def __init__(
        self, 
        estimator,         # объект модели (необученный)
        w: int = 3,        # ширина лага
        fill_val: Any = 0  # метка класса для первых w - 1 предсказаний
    ):
        self.estimator = estimator
        self.w = w
        self.fill_val = fill_val

    # Внутренний метод для формирования набора с лаговыми признаками
    def _make_lag(self, X: pd.DataFrame | np.ndarray):
        X_copy = np.array(X)
        w = self.w          # w - ширина лага
        n, m = X_copy.shape # n - кол-во строк, m - кол-во столбцов
            
        return np.vstack(
            [X_copy[i: i + w, :].reshape(m * w) for i in range(n - w + 1)]
        )

    def fit(self, X, y):
        # Обучаем модель на лаговых признаках. 
        # При этом первые w - 1 примеров исходных данных пропускаются 
        # и в обучении не участвуют 
        self.estimator.fit(self._make_lag(X), np.array(y)[self.w - 1:])
        # Скопируем атрибут модели .classes_ в соответсвутующий атрибут обёртки
        self.classes_ = self.estimator.classes_
        return self
    
    def predict(self, X):
        
        return np.hstack([
            # заполняем первые w - 1 "предсказанных" меток значением по умолчанию
            [self.fill_val] * (self.w - 1),
            # делаем предсказание на лаговых признаках        
            self.estimator.predict(self._make_lag(X))
        ])
    
    def predict_proba(self, X):
        classes = self.estimator.classes_
        n_classes = classes.shape[0]
        return np.vstack([
            # заполняем первые w - 1 "предсказанных" меток равновероятными значениями
            [[1 / n_classes] * n_classes] * (self.w - 1),
            # делаем предсказание на лаговых признаках        
            self.estimator.predict_proba(self._make_lag(X))
        ])
    
    def set_params(self, **params):
        # Все именованные арументы кроме перечисленных
        wrapper_params = ['w']
        for param in wrapper_params:
            if param in params:
                self.w = params.pop(param)
        # предназначены для оборачиваемой модели
        self.estimator.set_params(**params)

# Оборачиваем логистическую регрессию   
lr_lag = LagWrapper(LogisticRegression(C=200, max_iter=5000), w=5)
# Обучаем и предсказываем как обычную модель
lr_lag.fit(X_train_scaled, y_train)
y_pred = lr_lag.predict(X_test_scaled)
print(classification_report(y_test, y_pred, zero_division=0))


fig_data = X_test.copy()
fig_data['true'] = y_test * 100
fig_data['pred'] = y_pred * 100

# Добавим в визуализацию предсказанные вероятности классов
y_pred_proba = pd.DataFrame(
    lr_lag.predict_proba(X_test_scaled),
    columns=['proba_' + c for c in map(str, lr_lag.classes_)],
    index=fig_data.index
)
fig_data = pd.concat([fig_data, y_pred_proba * 100], axis=1)

fig = px.line(fig_data, width=1000, height=700, title=montage)
fig.update_traces(line=dict(width=1))

              precision    recall  f1-score   support

           0       0.97      0.98      0.98      2666
           1       0.98      0.97      0.98       249
           2       0.97      0.97      0.97       257
           3       0.99      0.93      0.96       234
           4       0.87      1.00      0.93       201
           5       0.95      0.82      0.88       262

    accuracy                           0.97      3869
   macro avg       0.95      0.94      0.95      3869
weighted avg       0.97      0.97      0.97      3869

